In [ ]:
from functools import reduce
import networkx as nx
import numpy.random
from colomoto.minibn import BooleanNetwork
import matplotlib.pyplot as plt
from IPython.display import display, Markdown

In [ ]:
def random_influence_graph(n, p_pos=0.6, **kwargs):
    """
    scale-free graph, where edges have probabibilty p_pos to be positive
    """
    g = nx.DiGraph(nx.scale_free_graph(n, **kwargs))
    signs = numpy.random.choice([-1,1], size=len(g.edges()), p=[1-p_pos,p_pos])
    for j, e in enumerate(g.edges(data=True)):
        e[2]["sign"] = signs[j]
    nx.relabel_nodes(g, dict(zip(range(n), ["a%d"%i for i in range(n)])), copy=False)
    return g

In [ ]:
def get_regulators(g, n):
    """
    returns the list of activators and list of inhibitors of node n in graph g
    """
    act, inh = [], []
    for m, _, s in g.in_edges(n, data="sign"):
        assert s in [1,-1]
        (act if s == 1 else inh).append(m)
    return act, inh

def inhibitors_dominant_dnf(g, bn, n):
    """
    returns a DNF encoding the inihibitor dominant rule for node n in graph g
    """
    act, inh = get_regulators(g, n)
    act = bn.vars(*act)
    inh = [~a for a in bn.vars(*inh)]
    if not act and not inh: # input node
        return bn.vars(n)[0]
    if not inh:
        clauses = act
    elif not act:
        clauses = [bn.ba.AND(*inh) if len(inh) > 1 else inh[0]]
    else:
        clauses = [bn.ba.AND(*[a]+inh) for a in act]
    return bn.ba.OR(*clauses) if len(clauses) > 1 else clauses[0]

def inhibitors_dominant_bn(g):
    bn = BooleanNetwork()
    for n, ind in g.in_degree():
        bn[n] = inhibitors_dominant_dnf(g, bn, n)
    return bn

In [ ]:
for n in [100000]:#[1000, 2000, 5000, 10000, 20000, 50000, 100000]:
    for i in range(1,5):
        display(Markdown(f"### {n} nodes ({i})"))
        
        # generate graph
        %time g = random_influence_graph(n, delta_in=2)
        
        # plot scatter in/out degrees
        nodes = list(g.nodes())
        degs = {
            "in": [i for _,i in g.in_degree(nodes)],
            "out": [i for _,i in g.out_degree(nodes)],
        }
        plt.plot("in", "out", data=degs, linestyle='none', marker='o')
        plt.xlabel("in")
        plt.ylabel("out")
        plt.show()
        
        # make Boolean networks with
        bn = inhibitors_dominant_bn(g)
        # save
        with open(f"random-{n}-{i}.bnet", "w") as fp:
            fp.write(bn.source())